In [2]:
%%capture
from pathlib import Path

if Path.cwd().stem == "notebooks":
    %cd ..
    %load_ext autoreload
    %autoreload 2

In [3]:
import logging
from pathlib import Path

import altair as alt
import holoviews as hv
import hvplot.polars  # noqa
import matplotlib.pyplot as plt
import numpy as np
import polars as pl
from polars import col

from src.data.database_manager import DatabaseManager
from src.features.labels import add_labels
from src.features.resampling import interpolate_and_fill_nulls
from src.features.scaling import scale_min_max
from src.features.transforming import map_trials, merge_dfs
from src.features.utils import to_describe
from src.log_config import configure_logging
from src.plots.confidence_intervals import plot_confidence_intervals
from src.plots.correlations import (
    aggregate_correlations_fisher_z,
    calculate_correlations_by_trial,
    plot_correlations_by_participant,
    plot_correlations_by_trial,
)
from src.plots.utils import prepare_multiline_hvplot

logger = logging.getLogger(__name__.rsplit(".", maxsplit=1)[-1])
configure_logging(
    stream_level=logging.DEBUG,
    ignore_libs=["matplotlib", "Comm", "bokeh", "tornado", "param", "numba"],
)

pl.Config.set_tbl_rows(12)  # for the 12 trials
hv.output(widget_location="bottom", size=130)

In [4]:
db = DatabaseManager()

In [ ]:
with db:
    pupil = db.get_table("Feature_Pupil")
    eda = db.get_table("Feature_EDA")
    ppg = db.get_table("Feature_PPG")
    stimulus = db.get_table("Feature_Stimulus")
    trials = db.get_table("Trials")

# Merge data dfs
df = merge_dfs([pupil, stimulus, eda, ppg])


# Add random walk column
def add_random_walk(group):
    return group.with_columns(
        walk=pl.Series(np.cumsum(np.random.normal(0, 1, len(group))))
    )


df = df.group_by("trial_id").map_groups(add_random_walk)

# Merge with trial metadata
df = merge_dfs(
    dfs=[df, trials],
    on=["trial_id", "participant_id", "trial_number"],
)
df = interpolate_and_fill_nulls(df)
# Rename columns
df = df.with_columns(col("pupil_mean").alias("pupil"))
df

shape: (10_055_808, 31)
┌──────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ trial_id ┆ trial_numb ┆ participa ┆ rownumber ┆ … ┆ timestamp ┆ timestamp ┆ duration  ┆ pupil    │
│ ---      ┆ er         ┆ nt_id     ┆ ---       ┆   ┆ _start    ┆ _end      ┆ ---       ┆ ---      │
│ u16      ┆ ---        ┆ ---       ┆ u32       ┆   ┆ ---       ┆ ---       ┆ f64       ┆ f64      │
│          ┆ u8         ┆ u8        ┆           ┆   ┆ f64       ┆ f64       ┆           ┆          │
╞══════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 1        ┆ 1          ┆ 1         ┆ 17631     ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.412048 │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ 1        ┆ 1          ┆ 1         ┆ null      ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.411348 │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ 1        ┆ 1          ┆ 1         ┆ null      ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.411286 │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ 1        ┆ 1          ┆ 1         ┆ 17632     ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.411025 │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ 1        ┆ 1          ┆ 1         ┆ null      ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.41049  │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ 1        ┆ 1          ┆ 1         ┆ 17633     ┆ … ┆ 294197.39 ┆ 474206.70 ┆ 180009.31 ┆ 5.409994 │
│          ┆            ┆           ┆           ┆   ┆ 45        ┆ 98        ┆ 53        ┆          │
│ …        ┆ …          ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …        │
│ 332      ┆ 12         ┆ 28        ┆ null      ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003387 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
│ 332      ┆ 12         ┆ 28        ┆ 166440    ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003369 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
│ 332      ┆ 12         ┆ 28        ┆ null      ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003326 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
│ 332      ┆ 12         ┆ 28        ┆ 166441    ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003315 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
│ 332      ┆ 12         ┆ 28        ┆ null      ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003315 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
│ 332      ┆ 12         ┆ 28        ┆ null      ┆ … ┆ 2.5971e6  ┆ 2.7771e6  ┆ 180026.12 ┆ 4.003315 │
│          ┆            ┆           ┆           ┆   ┆           ┆           ┆ 3         ┆          │
└──────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [ ]:
col1, col2 = "walk", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [53]:
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [19]:
col1, col2 = "temperature", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [7]:
col1, col2 = "pupil", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [8]:
scale_min_max(df).filter(col("trial_id") == 259).hvplot(
    x="timestamp", y=["pupil", "rating", "eda_tonic"]
)

:NdOverlay   [Variable]
   :Curve   [timestamp]   (value)

In [9]:
col1, col2 = "pupil", "temperature"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
# plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [10]:
col1, col2 = "eda_tonic", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [11]:
scale_min_max(df).filter(col("trial_id") == 202).hvplot(
    x="timestamp", y=["pupil", "rating", "eda_tonic"]
)

:NdOverlay   [Variable]
   :Curve   [timestamp]   (value)

In [12]:
col1, col2 = "eda_phasic", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [13]:
col1, col2 = "heartrate", "rating"

corr_by_trial = calculate_correlations_by_trial(df, col1, col2)
corr_by_participant = aggregate_correlations_fisher_z(
    corr_by_trial, f"{col1}_{col2}_corr", "participant_id", include_ci=True
)
plot_correlations_by_trial(corr_by_trial, f"{col1}_{col2}_corr")
# plot_correlations_by_participant(corr_by_participant, f"{col1}_{col2}_corr")

alt.LayerChart(...)

In [ ]:
scale_min_max(df).filter(col("participant_id") == 16).hvplot(
    x="timestamp", y=["heartrate", "rating"], groupby="trial_id"
)

BokehModel(combine_events=True, render_bundle={'docs_json': {'d4ba6cd2-2a17-4f3d-8b0c-17fc1ae343cb': {'version…

Hypothesis: mediated by respiration
-> instruct participants to exhale while pain decreases?